## Feature extraction 
Esta notebook está dedicada a la construcción de variables a partir de la data de EEG.  
Para un archivo con la lectura de EEG este script agrega:  
- bandas de frecuencia
- estadísticos de las bandas de frecuencia
- clustering (con k-means) de los momentos en el tiempo

In [ ]:
%%capture
!pip install mne

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import mne
import os

past_df_fnames = [
       "/content/drive/MyDrive/deep-self-lecturas/records_RAW/EEG_2022-04-28_191254.csv",
       "/content/drive/MyDrive/deep-self-lecturas/records_RAW/amigo_emotiv_EEG_2022-05-04_183959.csv",
       "/content/drive/MyDrive/deep-self-lecturas/records_RAW/visitaLUIS_EEG_2022-05-12_155743.csv",
       "/content/drive/MyDrive/deep-self-lecturas/records_RAW/visita_nom_metzli_EEG_2022-05-12_150718.csv",
       "/content/drive/MyDrive/deep-self-lecturas/records_RAW/visitanta_1_EEG_2022-05-04_125549.csv",
       "/content/drive/MyDrive/deep-self-lecturas/records_RAW/quetzalli_EEG_2022-04-30_134611.csv",
       "/content/drive/MyDrive/deep-self-lecturas/records_RAW/alf_audio_EEG_2022-04-20_155442.csv",
       "/content/drive/MyDrive/deep-self-lecturas/records_RAW/emme_audio_EEG_2022-04-28_145148.csv",
       "/content/drive/MyDrive/deep-self-lecturas/records_RAW/feli_audio_EEG_2022-04-28_174706.csv",
       "/content/drive/MyDrive/deep-self-lecturas/records_RAW/les_audio_EEG_2022-04-20_153820.csv",
       '/content/drive/MyDrive/deep-self-lecturas/records_RAW/daniel_nicksbro_EEG_2022-05-06_165529.csv',
       '/content/drive/MyDrive/deep-self-lecturas/records_RAW/vcamille_EEG_2022-05-14_174941.csv',
       '/content/drive/MyDrive/deep-self-lecturas/records_RAW/valfs_EEG_2022-05-14_182142.csv',
       '/content/drive/MyDrive/deep-self-lecturas/records_RAW/vvvv_EEG_2022-05-14_185826.csv',
       '/content/drive/MyDrive/deep-self-lecturas/records_RAW/jorgeglez_EEG_2022-05-14_184056.csv',
       '/content/drive/MyDrive/deep-self-lecturas/records_RAW/ROBERTO_EEG_2022-05-06_183202.csv',
]

path = '/content/drive/MyDrive/deep-self-lecturas/records_RAW/'
df_fnames = [path + f for f in os.listdir(path) if (path + f) not in past_df_fnames]

dfs = []
for fname in df_fnames:
  df = pd.read_csv(fname, header=0, index_col = False)
  #tomamos únicamente las lecturas que tienen más de 10 minutos 
  # (64 lecturas por 600 segundos)
  if len(df) > 64 * 600: 
    dfs.append(df)

In [ ]:
len(dfs)

12

In [ ]:
# nicksbro '/content/drive/MyDrive/deep-self-lecturas/records_RAW/daniel_nicksbro_EEG_2022-05-06_165529.csv',
# camil '/content/drive/MyDrive/deep-self-lecturas/records_RAW/vcamille_EEG_2022-05-14_174941.csv',
# valf '/content/drive/MyDrive/deep-self-lecturas/records_RAW/valfs_EEG_2022-05-14_182142.csv',
# vvvv '/content/drive/MyDrive/deep-self-lecturas/records_RAW/vvvv_EEG_2022-05-14_185826.csv',
# jorgegonzales '/content/drive/MyDrive/deep-self-lecturas/records_RAW/jorgeglez_EEG_2022-05-14_184056.csv',
# roberto '/content/drive/MyDrive/deep-self-lecturas/records_RAW/ROBERTO_EEG_2022-05-06_183202.csv',

# Analisis inicial


In [ ]:
# #define info EEG RAW
# sfreq = 64
# ch_types = ["eeg"]*5
# ch_names = ['AF3', 'T7', 'Pz', 'T8', 'AF4']
# montage = mne.channels.make_standard_montage("standard_1020")
# info = mne.create_info(ch_names=ch_names, sfreq=sfreq, ch_types=ch_types)
# samples = df[ch_names].T*1e-6
# loadedRaw = mne.io.RawArray(samples, info)
# loadedRaw.set_montage(montage = montage)

In [ ]:
# df[ch_names]

In [ ]:
# ica = mne.preprocessing.ICA(n_components=4)

In [ ]:
# loadedRaw.filter(1., None, n_jobs=1, fir_design='firwin')

In [ ]:
# ica.fit(loadedRaw)

In [ ]:
# ica_data = ica.get_sources(inst=loadedRaw).get_data()
# df['ICA_1'] = ica_data[0]
# df['ICA_2'] = ica_data[1]
# df['ICA_3'] = ica_data[2]

In [ ]:
# ica.plot_components(outlines="skirt")

## Ahora por epochs


In [ ]:
# Aquí estoy creando una epoch cada 64 pasos que es un segundo
# events = [[id*64, 0, id] for id in range(1,len(df)//64)]
# epochs = mne.Epochs(loadedRaw, events)

In [ ]:
# events

In [ ]:
# df['IC1_AF3'] = 

In [ ]:
# ica.fit(epochs[i])
# components = ica.get_components().T
# df.loc['IC1_AF3'] = components[0][1]
# # '  '.join([str(s) for s in components[0].tolist()])

In [ ]:
# for i in range(len(events)):
#     ica.fit(epochs[i])
#     ica.plot_components()

# Procesamiento en batch

In [ ]:
def augment_with_ica(df, n_components = 4):
    #define info EEG RAW
    sfreq = 64
    ch_types = ["eeg"]*5
    ch_names = ['AF3', 'T7', 'Pz', 'T8', 'AF4']
    df_ = df.dropna(subset = ch_names).copy()
    montage = mne.channels.make_standard_montage("standard_1020")
    info = mne.create_info(ch_names=ch_names, sfreq=sfreq, ch_types=ch_types)
    samples = df_[ch_names].T*1e-6
    loadedRaw = mne.io.RawArray(samples, info)
    loadedRaw.set_montage(montage = montage)

    ica = mne.preprocessing.ICA(n_components=n_components)

    filt_raw = loadedRaw.copy().filter(l_freq=1., h_freq=None)    
    
    ica.fit(filt_raw)

    ica_data = ica.get_sources(inst=loadedRaw).get_data()
    
    for n in range(n_components):
        df_['ICA_'+str(n + 1)] = ica_data[n]

    events = [[id*64, 0, id] for id in range(1,len(df)//64)]
    epochs = mne.Epochs(filt_raw, events)

    lower = 0
    for e, event in enumerate(events):
        upper = event[0]
        ica.fit(epochs[e])
        components = ica.get_components().T
        for n in range(n_components):
            for j, chan in enumerate(ch_names):
                df_.loc[lower:upper,'ICA_comp'+ str(n + 1) +'_' + chan] = components[n][j]

        lower = upper

    return df_



In [ ]:
def augment_with_brainwaves(df, channel = 'ICA_1'):

    df_ = df.copy()
    print ("shape of dataframe: {}".format(df.shape))

    # then make the windows and calculate
    # delta 0.1 - 3.5     fmed = 2
    # theta 4.0 - 8.0     fmed = 6
    # alpha 8.0 - 12.0    fmed = 10
    # l_beta 12.0 - 18.0  fmed = 15
    # h_beta 18.0 - 30.0  fmed = 25
    # gamma     > 30      fmed = 32

    freqs = [2, 6, 10, 15, 20, 30]
    dft = [[],[],[],[],[],[],[]]
    fnames = ["delta", "theta", "alpha", "beta_l", "beta_h", "gamma"]

    # use the window to calculate FFTs
    for i in range(len(df_[channel])):
      if i<64:
        win = np.zeros(64)
        win[-(i+1):] = df_[channel][:i+1]
      else:
        win[-i:] = df_[channel][i-64:i] 
      #print(win)
      # fft for the win
      fft_win = np.fft.fft(win) 
      for i,f in enumerate(freqs):
        dft[i].append(abs(fft_win[f]))

    # df is the last loaded dataframe
    # dft[i] got the list of fft coeficients for given freqs freqs[i]
    # then we need to save it to nu_files

    df_ = df_.assign(delta_ICA_1 = dft[0])
    df_ = df_.assign(theta_ICA_1 = dft[1])
    df_ = df_.assign(alpha_ICA_1 = dft[2])
    df_ = df_.assign(beta_l_ICA_1 = dft[3])
    df_ = df_.assign(beta_h_ICA_1 = dft[4])
    df_ = df_.assign(gamma_ICA_1 = dft[5])

    return df_




In [ ]:
import numpy as np
from sklearn.cluster import MiniBatchKMeans, KMeans
from sklearn.metrics import silhouette_samples, silhouette_score

def silhouette_score_get_k(X, k_range = (3, 10)):
    range_n_clusters = range(k_range[0], k_range[1])
    max_silhouette = -1
    best_k = 0

    for n_clusters in range_n_clusters:
        # The silhouette_score gives the average value for all the samples.
        # This gives a perspective into the density and separation of the formed
        # clusters
        cluster_labels = KMeans(n_clusters=n_clusters, random_state=0).fit_predict(X)
        silhouette_avg = silhouette_score(X, cluster_labels)
        print("For n_clusters =", n_clusters,
              "The average silhouette_score is :", silhouette_avg)
        # find maximum average silhouette to select the best 'k' value  
        if silhouette_avg > max_silhouette: 
          max_silhouette = silhouette_avg
          best_k = n_clusters

    print('Best k = '+str(best_k))
    return best_k

def augment_with_kmeans(df):

    df_ = df.copy()

    intermediate_df = df.copy()

    rolling_columns = ["ICA_1","ICA_2","ICA_3","ICA_4"]

    cluster_columns = rolling_columns

    # rolling_columns = ['delta_ICA_1', 'theta_ICA_1', 'alpha_ICA_1', 'beta_l_ICA_1','beta_h_ICA_1', 'gamma_ICA_1']
    rolling = intermediate_df.loc[:,rolling_columns].rolling(128).median()
    rolling.columns = [col + "_med" for col in rolling_columns]
    intermediate_df = pd.concat([intermediate_df, rolling],axis=1)
    cluster_columns = cluster_columns + [col + "_med" for col in rolling_columns]

    rolling = intermediate_df.loc[:,rolling_columns].rolling(128).std()
    rolling.columns = [col + "_std" for col in rolling_columns]
    intermediate_df = pd.concat([intermediate_df, rolling],axis=1)
    cluster_columns = cluster_columns + [col + "_std" for col in rolling_columns]
        
    rolling = intermediate_df.loc[:,rolling_columns].iloc[::-1].rolling(128).median()
    rolling.columns = [col + "_med-" for col in rolling_columns]
    intermediate_df = pd.concat([intermediate_df, rolling],axis=1)
    cluster_columns = cluster_columns + [col + "_med" for col in rolling_columns]

    rolling = intermediate_df.loc[:,rolling_columns].iloc[::-1].rolling(128).std()
    rolling.columns = [col + "_std-" for col in rolling_columns]
    intermediate_df = pd.concat([intermediate_df, rolling],axis=1)
    cluster_columns = cluster_columns + [col + "_std" for col in rolling_columns]
    
    intermediate_df = intermediate_df.dropna(subset=intermediate_df.columns.difference(['key', 'Unnamed: 6']))
    
    X=intermediate_df.loc[:,cluster_columns].to_numpy()

    # import pdb;pdb.set_trace()

    best_k = silhouette_score_get_k(X, k_range = (3,10))
    k_means = KMeans(init="k-means++", n_clusters=best_k, n_init=10)
    k_means.fit(X)
    Y = k_means.labels_
    df_ = df_.iloc[intermediate_df.index,:].assign(label=Y)

    return df_

In [ ]:
# dfx = augment_with_ica(df)
# dfx = augment_with_brainwaves(dfx)
# dfx = augment_with_kmeans(dfx)

In [ ]:
dfs_final = []
for i,df in enumerate(dfs):
  df_ = augment_with_ica(df)
  df_ = augment_with_brainwaves(df_)
  augment_with_kmeans(df_).to_csv('/content/drive/MyDrive/deep-self-lecturas/EEG-procesadas/' + df_fnames[i].split('/')[-1])
  print('/content/drive/MyDrive/deep-self-lecturas/EEG-procesadas/' + df_fnames[i].split('/')[-1])
  # dfs_final.append()

Creating RawArray with float64 data, n_channels=5, n_times=143432
    Range : 0 ... 143431 =      0.000 ...  2241.109 secs
Ready.
Filtering raw data in 1 contiguous segment
Setting up high-pass filter at 1 Hz

FIR filter parameters
---------------------
Designing a one-pass, zero-phase, non-causal highpass filter:
- Windowed time-domain design (firwin) method
- Hamming window with 0.0194 passband ripple and 53 dB stopband attenuation
- Lower passband edge: 1.00
- Lower transition bandwidth: 1.00 Hz (-6 dB cutoff frequency: 0.50 Hz)
- Filter length: 213 samples (3.328 sec)

Fitting ICA to data using 5 channels (please be patient, this may take a while)
Selecting by number: 4 components
Fitting ICA took 1.0s.
Not setting metadata
2240 matching events found
Setting baseline interval to [-0.203125, 0.0] sec
Applying baseline correction (mode: mean)
0 projection items activated
Fitting ICA to data using 5 channels (please be patient, this may take a while)
Using data from preloaded Raw for 

<ipython-input-6-a96e6b762b69>:30: RuntimeWarning: The epochs you passed to ICA.fit() were baseline-corrected. However, we suggest to fit ICA only on data that has been high-pass filtered, but NOT baseline-corrected.
  ica.fit(epochs[e])
<ipython-input-6-a96e6b762b69>:30: RuntimeWarning: The epochs you passed to ICA.fit() were baseline-corrected. However, we suggest to fit ICA only on data that has been high-pass filtered, but NOT baseline-corrected.
  ica.fit(epochs[e])


Fitting ICA to data using 5 channels (please be patient, this may take a while)
Using data from preloaded Raw for 1 events and 46 original time points ...
0 bad epochs dropped
Selecting by number: 4 components


<ipython-input-6-a96e6b762b69>:30: RuntimeWarning: The epochs you passed to ICA.fit() were baseline-corrected. However, we suggest to fit ICA only on data that has been high-pass filtered, but NOT baseline-corrected.
  ica.fit(epochs[e])


Using data from preloaded Raw for 1 events and 46 original time points ...
Fitting ICA took 0.3s.
Fitting ICA to data using 5 channels (please be patient, this may take a while)
Using data from preloaded Raw for 1 events and 46 original time points ...
0 bad epochs dropped
Selecting by number: 4 components
Using data from preloaded Raw for 1 events and 46 original time points ...
Fitting ICA took 0.0s.
Fitting ICA to data using 5 channels (please be patient, this may take a while)
Using data from preloaded Raw for 1 events and 46 original time points ...
0 bad epochs dropped
Selecting by number: 4 components
Using data from preloaded Raw for 1 events and 46 original time points ...
Fitting ICA took 0.0s.


...

Using data from preloaded Raw for 1 events and 46 original time points ...
Fitting ICA took 0.0s.
Fitting ICA to data using 5 channels (please be patient, this may take a while)
Using data from preloaded Raw for 1 events and 46 original time points ...
0 bad epochs dropped
Selecting by number: 4 components
Using data from preloaded Raw for 1 events and 46 original time points ...
Fitting ICA took 0.0s.
Fitting ICA to data using 5 channels (please be patient, this may take a while)
Using data from preloaded Raw for 1 events and 46 original time points ...
0 bad epochs dropped
Selecting by number: 4 components
Using data from preloaded Raw for 1 events and 46 original time points ...
Fitting ICA took 0.0s.
Fitting ICA to data using 5 channels (please be patient, this may take a while)
Using data from preloaded Raw for 1 events and 46 original time points ...
0 bad epochs dropped
Selecting by number: 4 components
Using data from preloaded Raw for 1 events and 46 original time points ...
F

<ipython-input-6-a96e6b762b69>:30: RuntimeWarning: The epochs you passed to ICA.fit() were baseline-corrected. However, we suggest to fit ICA only on data that has been high-pass filtered, but NOT baseline-corrected.
  ica.fit(epochs[e])
<ipython-input-6-a96e6b762b69>:30: RuntimeWarning: The epochs you passed to ICA.fit() were baseline-corrected. However, we suggest to fit ICA only on data that has been high-pass filtered, but NOT baseline-corrected.
  ica.fit(epochs[e])
<ipython-input-6-a96e6b762b69>:30: RuntimeWarning: The epochs you passed to ICA.fit() were baseline-corrected. However, we suggest to fit ICA only on data that has been high-pass filtered, but NOT baseline-corrected.
  ica.fit(epochs[e])


Fitting ICA to data using 5 channels (please be patient, this may take a while)
Using data from preloaded Raw for 1 events and 46 original time points ...
0 bad epochs dropped
Selecting by number: 4 components
Using data from preloaded Raw for 1 events and 46 original time points ...
Fitting ICA took 0.0s.
Fitting ICA to data using 5 channels (please be patient, this may take a while)
Using data from preloaded Raw for 1 events and 46 original time points ...
0 bad epochs dropped
Selecting by number: 4 components
Using data from preloaded Raw for 1 events and 46 original time points ...
Fitting ICA took 0.0s.
shape of dataframe: (39507, 31)


<ipython-input-6-a96e6b762b69>:30: RuntimeWarning: The epochs you passed to ICA.fit() were baseline-corrected. However, we suggest to fit ICA only on data that has been high-pass filtered, but NOT baseline-corrected.
  ica.fit(epochs[e])
<ipython-input-6-a96e6b762b69>:30: RuntimeWarning: The epochs you passed to ICA.fit() were baseline-corrected. However, we suggest to fit ICA only on data that has been high-pass filtered, but NOT baseline-corrected.
  ica.fit(epochs[e])


For n_clusters = 3 The average silhouette_score is : 0.6034387441093074
For n_clusters = 4 The average silhouette_score is : 0.19905149761295404
For n_clusters = 5 The average silhouette_score is : 0.18964081860486667
For n_clusters = 6 The average silhouette_score is : 0.19439300493877623
For n_clusters = 7 The average silhouette_score is : 0.201214425603304
For n_clusters = 8 The average silhouette_score is : 0.20530467951270226
For n_clusters = 9 The average silhouette_score is : 0.19507088784691737
Best k = 3
/content/drive/MyDrive/deep-self-lecturas/EEG-procesadas/EEG_2022-04-11_145221.csv


In [ ]:
# dfs = []
# for i,df in enumerate(dfs_final):
#     df.to_csv('/content/drive/MyDrive/deep-self-lecturas/EEG-procesadas/' + df_fnames[i].split('/')[-1])
#     print('/content/drive/MyDrive/deep-self-lecturas/EEG-procesadas/' + df_fnames[i].split('/')[-1])

In [ ]:
# dfs_final[0].columns